# Motive Engine

![](images/v3_slide0094_image039.gif)

The Motive Engine is based on opposing weights. An object signals it's presence if the Sim's need is low. The need is the motive and that drives a Sims' decision. All games in the franchise are based on this dynamic at it's core. For example, if hunger is low then the fridge's presence is high and vice versa. A Sim's mood is the sum of the current state of their motives. They will only choose the fridge if it increases it's overall mood. The ML portion comes in deciding which has the priority.

A Sim's motives decrease in increments and independently of each other during game play. They are randomized for this experiment. 

In [1]:
#r "nuget:Microsoft.ML"

In [1]:
using System.Linq;

In [1]:
const int NAX_MOOD = 600;
const int MAX_MOTIVE = 100;

In [1]:
static int MaxLimit(this int val, int max)
{
    if (max < 0)
        throw new ArgumentOutOfRangeException();

    if (val >= max)
        return max;

    return val;
}

In [1]:
class Motives
{
    public Motives(int hunger, int bladder, int fun, int energy, 
        int environment, int social)
    {
        Hunger = hunger;
        Bladder = bladder;
        Fun = fun;
        Energy = energy;
        Environment = environment;
        Social = social;
    }

    public int Hunger { get; set; }
    public int Bladder { get; set; }
    public int Fun { get; set; }
    public int Energy { get; set; }
    public int Environment { get; set; }
    public int Social { get; set; }

    // The mood is the sum of all the motives.
    // It deteremines the best course of action.
    public int Mood
    {
        get
        {
            var curMood = new[] { Hunger, Bladder, Fun,
                Social, Environment, Energy };

            return curMood.Sum();
        }
    }

    // In the game, this would increament gradually
    // until it reaches it's max motive.
    int CalcuateMotiveChange(int motive, int input)
    {
        var curMotive = motive;
        var curMood = Mood;

        // New motive equals the current motive plus the input
        var newMotive = curMotive + input;

        // New mood equals the new motive plus the current mood
        var newMood = newMotive + curMood;

        // Changed motive is the new motive with the limit
        var changedMotive = newMotive.MaxLimit(MAX_MOTIVE);

        // Does the new motive increase my current motive?
        // Does the new motive increase my overall mood?
        if (changedMotive >= curMotive && curMood <= NAX_MOOD 
            && changedMotive <= MAX_MOTIVE && curMood <= NAX_MOOD)
            return changedMotive;
        
        // Fall back to the current movement
        return curMotive;
    }

    public void ChangeHunger(int input)
    {
        Hunger = CalcuateMotiveChange(Hunger, input);
    }

    public void ChangeFun(int input)
    {
        Fun = CalcuateMotiveChange(Fun, input);
    }

    public void ChangeBladder(int input)
    {
        Bladder = CalcuateMotiveChange(Bladder, input);
    }

    public void ChangeSocial(int input)
    {
        Social = CalcuateMotiveChange(Social, input);
    }

    public void ChangeEnergy(int input)
    {
        Energy = CalcuateMotiveChange(Energy, input);
    }

    public void ChangeEnvironment(int input)
    {
        Environment = CalcuateMotiveChange(Environment, input);
    }
}

In [1]:
void PrintMotives(Motives motives)
{
    Console.WriteLine($"Hunger: {motives.Hunger}{Environment.NewLine}" +
        $"Fun: {motives.Fun}{Environment.NewLine}" +
        $"Bladder: {motives.Bladder}{Environment.NewLine}" +
        $"Social: {motives.Social}{Environment.NewLine}" +
        $"Environment: {motives.Environment}");
    Console.WriteLine($"Mood: {motives.Mood}");
}

In [1]:
// Run this first
var rng = new Random();

var motives = new Motives(hunger: rng.Next(MAX_MOTIVE), 
bladder: rng.Next(MAX_MOTIVE), fun: rng.Next(MAX_MOTIVE), 
energy: rng.Next(MAX_MOTIVE),  environment: rng.Next(MAX_MOTIVE), 
social: rng.Next(MAX_MOTIVE));

PrintMotives(motives);

In [1]:
// Run this next
var newRng = new Random();

// Minimum random number is whatever the current motive is
motives.ChangeHunger(newRng.Next(motives.Hunger, MAX_MOTIVE));
motives.ChangeFun(newRng.Next(motives.Fun, MAX_MOTIVE));
motives.ChangeSocial(newRng.Next(motives.Social, MAX_MOTIVE));
motives.ChangeBladder(newRng.Next(motives.Bladder, MAX_MOTIVE));
motives.ChangeEnergy(newRng.Next(motives.Energy, MAX_MOTIVE));
motives.ChangeEnvironment(newRng.Next(motives.Environment, MAX_MOTIVE));

PrintMotives(motives);